# Moving car example by using speos files combination

This tutorial demonstrates how to run moving car workflow use case.

In [1]:
import os
from pathlib import Path

from ansys.speos.core import Part, Speos
from ansys.speos.core.sensor import SensorCamera
from ansys.speos.core.simulation import SimulationInverse
from ansys.speos.core.source import SourceLuminaire
from ansys.speos.core.workflow.combine_speos import (
    SpeosFileInstance,
    combine_speos,
)

# If using docker container
assets_data_path = Path("/app") / "assets"
# If using local server
# assets_data_path = Path().resolve().parent.parent / "tests" / "assets"
# If using a different path
# assets_data_path = Path("path/to/downloaded/example/assets")

## Create connection with speos rpc server

In [2]:
speos = Speos(host="localhost", port=50098)

## Combine several speos files into one project

Here we are building a project with:
- An environment which is a road
- A blue car
- A red car

In [3]:
p = combine_speos(
    speos=speos,
    speos_to_combine=[
        SpeosFileInstance(
            speos_file=str(assets_data_path / "Env_Simplified.speos" / "Env_Simplified.speos"),
            axis_system=[0, 0, 0, 1, 0, 0, 0, 1, 0, 0, 0, 1],
        ),
        SpeosFileInstance(
            speos_file=str(assets_data_path / "BlueCar.speos" / "BlueCar.speos"),
            axis_system=[
                2000,
                0,
                35000,
                0.0,
                0.0,
                -1.0,
                -1.0,
                0.0,
                0.0,
                0.0,
                1.0,
                0.0,
            ],
        ),
        SpeosFileInstance(
            speos_file=str(assets_data_path / "RedCar.speos" / "RedCar.speos"),
            axis_system=[
                -4000,
                0,
                48000,
                1.0,
                0.0,
                0.0,
                0.0,
                0.0,
                -1.0,
                0.0,
                1.0,
                0.0,
            ],
        ),
    ],
)
print(p)

{
    "part_guid": "9a146d7b-924d-4828-8012-1ad96e0af8d8",
    "materials": [
        {
            "name": "Env_Simplified.Material.1",
            "metadata": {
                "UniqueId": "fbf39463-9a33-41ec-b909-c38b6de1a62c"
            },
            "vop_guid": "9531003f-574a-461f-bbc4-b2d8a44db2c1",
            "sop_guids": [
                "4ca7bf1d-efaf-4844-a447-b2167c738edc"
            ],
            "geometries": {
                "geo_paths": [
                    "Env_Simplified/Sidewalk:530980414"
                ]
            },
            "description": "",
            "vop": {
                "opaque": {},
                "name": "",
                "description": "",
                "metadata": {}
            },
            "sops": [
                {
                    "library": {
                        "sop_file_uri": "/app/assets/Env_Simplified.speos/Side Walk_33b4-3fff-6c8d-7671..scattering"
                    },
                    "name": "",
          

## Preview the project

User can review the created/loaded project using preview method.

In [4]:
p.preview()

EmbeddableWidget(value='<iframe srcdoc="<!DOCTYPE html>\n<html>\n  <head>\n    <meta http-equiv=&quot;Content-…

## Complete the project with sensor/source/simulation

We are adding a camera sensor to have output results, a luminaire to have a light source.

And, we gather the source and the sensor into a simulation (we will compute it just after).

### Create a sensor

In [5]:
ssr = p.create_sensor(name="Camera.1", feature_type=SensorCamera)
ssr.set_distortion_file_uri(
    uri=str(assets_data_path / "CameraInputFiles" / "CameraDistortion_190deg.OPTDistortion")
).set_mode_photometric().set_transmittance_file_uri(
    uri=str(assets_data_path / "CameraInputFiles" / "CameraTransmittance.spectrum")
).set_mode_color().set_red_spectrum_file_uri(
    uri=str(assets_data_path / "CameraInputFiles" / "CameraSensitivityRed.spectrum")
).set_blue_spectrum_file_uri(
    uri=str(assets_data_path / "CameraInputFiles" / "CameraSensitivityBlue.spectrum")
).set_green_spectrum_file_uri(
    uri=str(assets_data_path / "CameraInputFiles" / "CameraSensitivityGreen.spectrum")
)
ssr.set_axis_system([-2000, 1500, 11000, -1, 0, 0, 0, 1, 0, 0, 0, -1])
ssr.commit()

### Create a source

In this example, a luminaire source is created with an IES file.

More details on creating/editing source examples can be found in core examples.

In [6]:
src = p.create_source(name="Luminaire.1", feature_type=SourceLuminaire)
src.set_intensity_file_uri(
    uri=str(assets_data_path / "IES_C_DETECTOR.ies")
).set_spectrum().set_daylightfluorescent()
src.set_axis_system([0, 10000, 50000, 1, 0, 0, 0, 1, 0, 0, 0, 1])
src.commit()

### Create a simulation

More details on creating/editing simulation examples can be found in core examples.

In [7]:
sim = p.create_simulation(name="Inverse.1", feature_type=SimulationInverse)
sim.set_sensor_paths(["Camera.1"]).set_source_paths(["Luminaire.1"])
sim.commit()

## Run the simulation

Simulation can be run using CPU via compute_CPU method or using GPU via compute_GPU method.

In [8]:
sim.compute_CPU()  # run simulation in CPU
# sim.compute_GPU()  # run simulation in GPU

[upload_response {
  info {
    uri: "3aae8918-1393-443d-a436-cff0b38b7c6b"
    file_name: "Camera.1.Irradiance.xmp"
    file_size: 10645308
  }
  upload_duration {
    nanos: 12833095
  }
}
, upload_response {
  info {
    uri: "23f6319a-7e2f-4527-8ec7-8607d4036a8a"
    file_name: "Camera.1.hdr"
    file_size: 518875
  }
  upload_duration {
    nanos: 943345
  }
}
, upload_response {
  info {
    uri: "faf728ba-8326-4d05-89c4-1ec945d31568"
    file_name: "Camera.1.xmp"
    file_size: 1805098
  }
  upload_duration {
    nanos: 2133312
  }
}
, upload_response {
  info {
    uri: "4a42dda3-bdb8-41b9-8471-7897ca6d5fc9"
    file_name: "Camera.1.png"
    file_size: 741878
  }
  upload_duration {
    nanos: 969434
  }
}
, upload_response {
  info {
    uri: "a192310b-55bf-411b-b2d7-bf301ff335cb"
    file_name: "Inverse.1.html"
    file_size: 998791
  }
  upload_duration {
    nanos: 1197771
  }
}
]

## Check and review result

Open result (only windows)

In [9]:
if os.name == "nt":
    from ansys.speos.core.workflow.open_result import open_result_image

    open_result_image(simulation_feature=sim, result_name="Camera.1.png")

## Modify part

Move the part via changing the axis_system of a part.

axis_system is a list of 12 float values:
x, y, z,
x_vect_x, x_vect_y, x_vect_z,
y_vect_x, y_vect_y, y_vect_z,
z_vect_x, z_vect_y, z_vect_z.

In [10]:
blue_car_sub_part = p.find(name="BlueCar", feature_type=Part.SubPart)[0]
blue_car_sub_part.set_axis_system([2000, 0.0, 20000, 0.0, 0.0, -1.0, -1.0, 0.0, 0.0, 0.0, 1.0, 0.0])
blue_car_sub_part.commit()

Re-run simulation with the modified part position

In [11]:
sim.compute_CPU()

[upload_response {
  info {
    uri: "1166444c-d223-4f5a-aee0-9a5fa7f7a93e"
    file_name: "Camera.1.Irradiance.xmp"
    file_size: 10395961
  }
  upload_duration {
    nanos: 10643875
  }
}
, upload_response {
  info {
    uri: "da1d5edb-eaf2-41bf-a8b4-9e36e3a538eb"
    file_name: "Camera.1.hdr"
    file_size: 519951
  }
  upload_duration {
    nanos: 778387
  }
}
, upload_response {
  info {
    uri: "cc9eac3d-58ca-4192-bfdb-16f02e080327"
    file_name: "Camera.1.xmp"
    file_size: 1763696
  }
  upload_duration {
    nanos: 2251956
  }
}
, upload_response {
  info {
    uri: "a4c0c7f0-20b5-424b-beef-1a90b7a0e3ff"
    file_name: "Camera.1.png"
    file_size: 728294
  }
  upload_duration {
    nanos: 986186
  }
}
, upload_response {
  info {
    uri: "186eb410-3f5f-4b64-822a-a53682e14969"
    file_name: "Inverse.1.html"
    file_size: 981557
  }
  upload_duration {
    nanos: 1237907
  }
}
]

Review result:

In [12]:
if os.name == "nt":
    open_result_image(simulation_feature=sim, result_name="Camera.1.png")

## Modify camera property

Modify the camera, e.g. focal length to 10

In [13]:
cam1 = p.find(name="Camera.1", feature_type=SensorCamera)[0]
cam1.set_focal_length(value=10)
cam1.commit()

Re-run the simulation and review result

In [14]:
sim.compute_CPU()
if os.name == "nt":
    open_result_image(simulation_feature=sim, result_name="Camera.1.png")